In [25]:
from time import time
from datetime import datetime
import numpy as np
seq = 10
dt = 8  
def multiply(A,B):
    return [a*b for a,b in zip(A,B)]
def divide(A,B):
    return [a/b for a,b in zip(A,B)]

def minus(A,B):
    return [a-b for a,b in zip(A,B)]
def log(txt):
    f= open("log%i.txt"%seq,"a+")
    f.write('%s: %s \r\n'%(datetime.now().strftime('{%Y-%m-%d %H:%M:%S}'),txt))
    print(txt)
    f.close() 
def initial_log():
    f= open("log%i.txt"%seq,"w+")
    f.write('%s: starting.... \r\n'%(datetime.now().strftime('{%Y-%m-%d %H:%M:%S}')))
    f.close() 
import pickle

def savedf():
    with open('df%i.dat'%dt,'wb') as f:
        pickle.dump((X_train, X_test, y_train, y_test),f)

def loaddf():
    global X_train, X_test, y_train, y_test
    with open('df%i.dat'%dt,'rb') as f:
        X_train, X_test, y_train, y_test = pickle.load(f)
    print("Shape of X_train:", len(X_train),len(X_train[0]))
    print("Shape of X_test:",len(X_test),len(X_test[0]))

      
def save():
    with open('data%i.dat'%seq,'wb') as f:
        pickle.dump((i,mdl_1,mdl_2,mdl_3,RMSETest,RMSETrain,last_depth,last_rmse),f)
def load():
    global i,mdl_1,mdl_2,mdl_3,RMSETest,RMSETrain,last_depth,last_rmse
    with open('data%i.dat'%seq,'rb') as f:
        i,mdl_1,mdl_2,mdl_3,RMSETest,RMSETrain,last_depth,last_rmse = pickle.load(f)

def load1():
    global i,mdl_1,mdl_2,mdl_3,RMSETest,RMSETrain,last_depth,last_rmse
    with open('data4.dat','rb') as f:
        i,mdl_1,mdl_2,mdl_3,RMSETest,RMSETrain,last_depth,last_rmse = pickle.load(f)
import os
os.environ["PATH"] += os.pathsep +"C:\\Users\\User\\Downloads\\graphviz-2.38\\release\\bin"


In [26]:
from numpy import var

class Splitter:
    def __init__(self,X,Y):
        self.X = X
        self.Y = Y

    def split(self,index,value):
        """ 
        Split X and Y based on the given variable index and value
  
        Parameters: 
            index (int): index of variable to splitted on
            value (float): the value of splitting varaible
          
        Returns: 
            right_x,left_x,rigth_y,left_y
        """
        right_x = [x for x in self.X if x[index]>=value]
        left_x = [x for x in self.X if x[index]<value]
        
        right_y = [self.Y[i] for i,x in enumerate(self.X) if x[index]>=value]
        left_y = [self.Y[i] for i,x in enumerate(self.X) if x[index]<value]
        return right_x,left_x,right_y,left_y
    
    def weighted_var(self,Y):
        if len(Y) ==0:
            return float('inf')
        return var(Y)/len(Y)
    
    def SE(self,Y):
        if len(Y) ==0: return float('inf')
        mean = sum(Y)/len(Y)
        SE = sum([(y-mean)**2 for y in Y])
        return SE
        
    
    def splitting_cost(self,right_x,left_x,right_y,left_y):
        """ 
        Compute cost of spliting.
        in the current version, we have used varaince based cost function
  
        Parameters: 
            right_x,left_x,rigth_y,left_y
          
        Returns: 
            float: the cost of computing
        """        
        return (self.SE(right_y)+self.SE(left_y))/(len(right_y)+len(left_y))
    
    def possibleValues(self,index):
        values = [x[index] for x in self.X]
        values.sort()
        max_values = 100
        if len(values)<max_values:
            return values
        
        return set([np.percentile(values,i*100//max_values) for i in range(max_values)])
    
    def test_splitting(self,index,value):
        right_x,left_x,right_y,left_y = self.split(index,value)
        return  self.splitting_cost(right_x,left_x,right_y,left_y),len(right_y),len(left_y)
    
    def find_best_splitting(self,min_leaf_treshold=0,min_split=0):
        """ 
        Find best splitting and return index and value of splitting variable respectively
       
        Returns: 
            int,float: the index and value of best possible splitting variables
        """ 
        
        best_splitting = (self.SE(self.Y)/len(self.Y))
        best_splitting_index = -1
        best_splitting_value = 0
        if len(self.Y)<min_split:
            return best_splitting_index,best_splitting_value            
        for index in range(len(self.X[0])):
            for value in self.possibleValues(index):
                splitting_cost,left_cnt,right_cnt = self.test_splitting(index,value)
#               print('splitting at %f: cost->%f'%(value,splitting_cost))
                if splitting_cost < best_splitting and left_cnt >= min_leaf_treshold and right_cnt >= min_leaf_treshold:
                    best_splitting = splitting_cost
                    best_splitting_index = index
                    best_splitting_value = value
        return best_splitting_index,best_splitting_value


In [27]:
id = 0
last_leaf_no = 1
j = 0
def create_Tree():
    global last_leaf_no
    last_leaf_no = 1
    return Node(0)
class Node:
    isLeaf = True
    Left = None
    Right = None
    Value = None
    Depth = 0
    splitting_var_index = 0
    splitting_value = 0
    cnt = 0
    
    
    def __init__(self,depth):
        global id
        id+=1
        self.ID = id
        self.isLeaf = True
        self.Depth = depth
    def predict(self,X):
        return [self.predict_one(x).Value for x in X]
        
    def predict_one(self,X):
        if type(X) != list:
            raise TypeError("predict_one.X: expected list but recieved %s (%s)"%(X,type(X)))
        try:
            if self.isLeaf:
                self.cnt +=1
                return self
            if X[self.splitting_var_index] >= self.splitting_value:
                return self.Right.predict_one(X)
            else:
                return self.Left.predict_one(X)
        except IndexError:
            print('index: %i'%self.splitting_var_index)
            raise
    def get_leafs(self):
        if self.isLeaf:
            return [self]
        return self.Right.get_leafs()+self.Left.get_leafs()   
    
    def fit(self,X,Y,max_depth):
        global last_leaf_no

        #tree reached maximum depth
        if max_depth <= self.Depth:
            self.isLeaf = True
            self.leafID = last_leaf_no
            last_leaf_no+=1
            self.fit_leaf_value(Y)
            return 
        
        #continue splitting if more depth allowed
        splitter = Splitter(X,Y)
        best_splitting_index,best_splitting_value = splitter.find_best_splitting()
        if best_splitting_index == -1:
            #better to not split
            self.isLeaf = True
            self.leafID = last_leaf_no
            last_leaf_no+=1
            self.fit_leaf_value(Y)
        else:
            right_x,left_x,right_y,left_y = splitter.split(best_splitting_index,best_splitting_value)
            self.isLeaf = False
            self.splitting_var_index = best_splitting_index
            self.splitting_value = best_splitting_value
            self.Right = Node(self.Depth+1)
            self.Left = Node(self.Depth+1)
            self.Right.fit(right_x,right_y,max_depth)
            self.Left.fit(left_x,left_y,max_depth)
    def fit_leaf_value(self,Y):
        self.Value = sum(Y)/len(Y)

        
    def tune(self,X,R,T):
        #self.X = X
       # self.Y = ['%f:%f'%(r,t) for r,t in zip(R,T)]
        if len(X) != len(R):
            raise TypeError("tune function: X and R should be with same size. recieved <%i>.<%i>"%(len(X),len(R)))
        if len(X) != len(T):
            raise TypeError("tune function: X and T should be with same size. recieved <%i>.<%i>"%(len(X),len(T)))
            
        if self.isLeaf:
            if sum(multiply(T,T)) == 0:
                self.value = 1
            else:
                self.Value = sum(multiply(R,T))/sum(multiply(T,T))
            return
        
        splitter = Splitter(X,R)
        right_x,left_X,right_R,left_R = splitter.split(self.splitting_var_index,self.splitting_value)
        splitter = Splitter(X,T)
        right_x,left_X,right_T,left_T = splitter.split(self.splitting_var_index,self.splitting_value)
        self.Right.tune(right_x,right_R,right_T)
        self.Left.tune(left_X,left_R,left_T)
        
    def draw_tree(self):
        global j
        from graphviz import Source
        from io import BytesIO
        import time
        timestr = time.strftime("%Y%m%d-%H%M%S")
        from matplotlib import pyplot as plt
        from matplotlib import image
        g = Source('digraph {\n\tgraph [rankdir=UT]\n'+self.print_tree()+'}')
        g.render('round-table%i.gv'%j, view=True)
        j+=1
        #return img
        
    def get_leafcounts(self):
        if self.isLeaf:
            return 1
        return self.Left.get_leafcounts()+self.Right.get_leafcounts()
    
    def print_tree(self,prefix=''):
        '\t0 [label="f0<8.40779079e-45] yes=1,no=2,missing=1\n\t1:[f0<2.80259693e-45] yes=3,no=4,missing=3\n\t\t3:leaf=7.46349096\n\t\t4:leaf=-0.278686523\n\t2:[f0<8.40779079e-45] yes=5,no=6,missing=5\n\t\t5:leaf=-0\n\t\t6:leaf=-0.188493282\n'
        if not self.isLeaf:
            ret = '\t%i [label="f%i>=%f"]\n\t%i -> %i [label="yes" color="#0000FF"]\n\t %i -> %i [label=no color="#FF0000"]\n'%(
                self.ID,self.splitting_var_index,self.splitting_value,self.ID,self.Right.ID,self.ID,self.Left.ID)
            ret += self.Right.print_tree(prefix+'\t')
            ret += self.Left.print_tree(prefix+'\t')
            return ret
        else:
            return '\t%i [label="leaf=%f\nCount=%i"]\n'%(self.ID,self.Value,self.cnt)
    def get_leaf_values(self):
        if self.isLeaf:
            return [self.Value]
        return self.Right.get_leaf_values()+self.Left.get_leaf_values()
    
'''digraph {
	graph [rankdir=UT]
	0 [label="f0<8.40779079e-45"]
	0 -> 1 [label="yes, missing" color="#0000FF"]
	0 -> 2 [label=no color="#FF0000"]
	1 [label="f0<2.80259693e-45"]
	1 -> 3 [label="yes, missing" color="#0000FF"]
	1 -> 4 [label=no color="#FF0000"]
	3 [label="leaf=7.46349096"]
	4 [label="leaf=-0.278686523"]
	2 [label="f0<8.40779079e-45"]
	2 -> 5 [label="yes, missing" color="#0000FF"]
	2 -> 6 [label=no color="#FF0000"]
	5 [label="leaf=-0"]
	6 [label="leaf=-0.188493282"]
}'''       
        

'digraph {\n\tgraph [rankdir=UT]\n\t0 [label="f0<8.40779079e-45"]\n\t0 -> 1 [label="yes, missing" color="#0000FF"]\n\t0 -> 2 [label=no color="#FF0000"]\n\t1 [label="f0<2.80259693e-45"]\n\t1 -> 3 [label="yes, missing" color="#0000FF"]\n\t1 -> 4 [label=no color="#FF0000"]\n\t3 [label="leaf=7.46349096"]\n\t4 [label="leaf=-0.278686523"]\n\t2 [label="f0<8.40779079e-45"]\n\t2 -> 5 [label="yes, missing" color="#0000FF"]\n\t2 -> 6 [label=no color="#FF0000"]\n\t5 [label="leaf=-0"]\n\t6 [label="leaf=-0.188493282"]\n}'

In [28]:
    from copy import deepcopy
    from sklearn.metrics import mean_squared_error
    from math import sqrt
    from scipy.sparse import csr_matrix
    from scipy import sparse
    import numpy as np
    from scipy.optimize import lsq_linear
    from sklearn.model_selection import train_test_split

    class FractBoosting:

        def __init__(self,learning_rate):
            self.learning_rate = learning_rate
            self.trees = []

        def predict(self,X,ignore_last=0):
            Y = []
            tree_filtered = self.trees[:max(1,len(self.trees)-ignore_last)]
            print('prediciting using %i trees'%len(tree_filtered))
            for x in X:
                predictions = [S.predict([x])[0]*T.predict([x])[0] for S,T in tree_filtered]
                predict = predictions[0] + self.learning_rate*sum(predictions[1:])
                Y.append(predict)

            return Y

        def fit(self,X,Y,max_depth,max_trees):
            """ 
            Fit the boosting trees on the given data

            Parameters: 
                X (list of list): the input X
                Y (list): input Y
                max_depth (int): maximum depth of trees
                max_trees (int): the number of trees
            """ 

            lastRMSE = self.rmse(X,Y)
            improvment = []
            for i in range(1,max_trees):
                t0 = time()
                depth = int(1+max_depth*sqrt(i/max_trees))
                log('starting itteration %i with depth %i'%(i,depth))
    #            print('itteration %i, begining, mean loss: %f, tree depth: %i'%(i,self.rmse(X,Y),depth))
                self.fit_one_step(X,Y,depth)

                current_rmse = self.rmse(X,Y)
                RMSEDif = lastRMSE - current_rmse
                lastRMSE = current_rmse
                cost = T.get_leafcounts()
                imp = cost/RMSEDif
                improvment.append(imp)
                log('itteration %i done in %0.3fs, RMSE: %f, Cost/improvement: %f'%(i,time() - t0,current_rmse,imp))
            return improvment
        def create_root_tree(self,Y):
            root_s = create_Tree()
            root_s.Value = 1
            root_t = create_Tree()
            root_t.fit_leaf_value(Y)
            self.trees = [(root_s,root_t)]

        def fit_one_step(self,X_TRAIN,Y_TRAIN,depth,backprop_level):
            X, X1, Y, Y1 = train_test_split(X_TRAIN, Y_TRAIN, test_size=0.2)
            Y_r = self.get_residual(X,Y)
            T = create_Tree()
            T.fit(X,Y_r,depth)
            Y_t = T.predict(X)
            S = deepcopy(self.trees[-1][1])
            S.tune(X,Y_r,Y_t)
            self.trees.append((S,T))
            X, _, Y, _ = train_test_split(X_TRAIN, Y_TRAIN, test_size=0.8)
            X = X+X1
            Y = Y+Y1
            self.back_prop(X,Y,backprop_level)
            
        def back_prop(self,X,Y,level):
            global A4
            print(len(X),len(Y))
            #self.trees[-1][0].draw_tree()
            h = self.predict(X,level)
            R = np.array(minus(Y , h))
            tr = self.trees[max(1,len(self.trees)-level):]
            print('computing last %i trees of S [total trees: %i]'%(len(tr),len(self.trees)))
            i = 0
            S_nodes =[]
            s_values = []
            for s,_ in tr:
                for leaf in s.get_leafs():
                    leaf.leaf_index = i
                    i+=1
                    S_nodes.append(leaf)
                    s_values.append(leaf.Value)
            row = []
            col = []
            data =[]
            for i,x in enumerate(X):
                for s,t in tr:
                    s_leaf = s.predict_one(x)
                    t_leaf = t.predict_one(x)
                    row.append(i)
                    col.append(s_leaf.leaf_index)
                    data.append(t_leaf.Value)
            A = sparse.csr_matrix((data, (row, col)), shape=(len(X), len(S_nodes))) 
            ##U = A.transpose().dot(A).todense()
            #V = A.transpose().dot(R)
            #A4 = np.linalg.pinv(U,hermitian =True).dot(V)
            #print(A4.shape)
            A4 = lsq_linear(A,R, bounds=(-0.01, .1)).x
            print("S Values before ",s_values)
            print('S Values after ',A4)
            #A4 = A4.todesne()
#            A1 = A.transpose().dot(A)
#            print(np.linalg.matrix_rank(A.todense()),np.linalg.matrix_rank(A1.todense()))
#            A2 = sparse.csr_matrix(inv(A1))
#            A3 = A.transpose().dot(R)
#            A4 = (A2.dot(A3)).todense()
            print('rmse before:',self.rmse(X,Y))
            r1 = self.get_residual(X,Y)
            for i,s1 in enumerate(S_nodes):
                s1.Value = A4[i]
            #self.trees[-1][0].draw_tree()
            print('rmse after:',self.rmse(X,Y))
            r2 = self.get_residual(X,Y)
            #print('Residual before ',r1)
            #print('Residual after ',r2)
            #print('diff ',minus(r1,r2))
            
        def get_residual(self,X,Y):
            h = self.predict(X)
            Y_r = minus(Y , h)
            return Y_r
        def print_trees(self):
            for i,(s,t) in enumerate(self.trees):
                print('%ith fractal tree\n'%i)
                print('-----------------\n')
                print('S:\n')
                s.print_tree()
                print('-----------------\n')
                print('T:\n')
                t.print_tree()
                print('\n-----------------\n')

        def rmse(self,X,Y):
            h = self.predict(X)
    #        R = minus(Y , h)
    #        print('Residual:',R)
            return sqrt(mean_squared_error(h, Y))


In [29]:
from numpy import std
import xgboost as xgb
from threading import Thread
from xgboost import plot_tree
from sklearn.metrics import mean_squared_error
max_depth=5

loaddf()
#initial_log()
mdl_1 = FractBoosting(1)
mdl_2 = FractBoosting(1)
mdl_3 = FractBoosting(1)
mdl_1.create_root_tree(y_train)
mdl_2.create_root_tree(y_train)
mdl_3.create_root_tree(y_train)
last_rmse = mdl_3.rmse(X_train,y_train)
last_depth = 1

m = sum(y_train)/len(y_train)
y_train_xgb = [y-m for y in y_train]

RMSETest = [[],[],[],[],[],[]]
RMSETrain =  [[],[],[],[],[],[]]
i=0
try:
    load()
    i
except Exception as e:
    print(e)
    initial_log()
try:
    while i<200:
        processes = []




        ################Fixed depth
        mdl_1.fit_one_step(X_train,y_train,max_depth,1)
        RMSETrain[0].append( mdl_1.rmse(X_train,y_train))
        RMSETest[0].append( mdl_1.rmse(X_test,y_test))    
        print('1 Back')


        
        ###############Linear depth
        #depth = min(5,int(1+max_depth*(i/50)))
        mdl_2.fit_one_step(X_train,y_train,max_depth,10)  
        RMSETrain[1].append( mdl_2.rmse(X_train,y_train))
        RMSETest[1].append( mdl_2.rmse(X_test,y_test))    
        print('2 Back')


        ###############dynamic depth
        mdl_3.fit_one_step(X_train,y_train,max_depth,20)
        #mdl3_rmse = mdl_3.rmse(X_test,y_test)
        RMSETrain[2].append( mdl_3.rmse(X_train,y_train))
        RMSETest[2].append( mdl_3.rmse(X_test,y_test))
        print('3 Back')
        


        ##################XGBoost
        xg_reg = xgb.XGBRegressor( learning_rate = 0.1,
                        max_depth = 5,  n_estimators = i)
        xg_reg.fit(X_train,y_train_xgb)    
        preds = xg_reg.predict(X_train)
        RMSETrain[3].append(np.sqrt(mean_squared_error(y_train, [p+m for p in preds])))
        preds = xg_reg.predict(X_test)
        RMSETest[3].append(np.sqrt(mean_squared_error(y_test, [p+m for p in preds])))
        print('XGB')
        i+=1
        
        save()
                           
        log('\r\n-----------------------------------------------\r\n'+
            'ittr %i  \tTrain\t\tTest\t\tDiff\t\tRVar\tSVar\tTVar\r\n'%i+
            'FGB[%i]:  \t%.3f\t\t%.3f\t\t%.3f\t\t%.3f\t%.3f\t\t%.3f\r\n'%(1,RMSETrain[0][-1],RMSETest[0][-1],RMSETest[0][-1]-RMSETrain[0][-1],std(mdl_1.get_residual(X_train,y_train)),std(mdl_1.trees[-1][0].get_leaf_values()),std(mdl_1.trees[-1][1].get_leaf_values()))+
            'FGB[%i]:  \t%.3f\t\t%.3f\t\t%.3f\t\t%.3f\t%.3f\t\t%.3f\r\n'%(10,RMSETrain[1][-1],RMSETest[1][-1],RMSETest[1][-1]-RMSETrain[1][-1],std(mdl_2.get_residual(X_train,y_train)),std(mdl_2.trees[-1][0].get_leaf_values()),std(mdl_2.trees[-1][1].get_leaf_values()))+
            'FGB[%i]:  \t%.3f\t\t%.3f\t\t%.3f\t\t%.3f\t%.3f\t\t%.3f\r\n'%(20,RMSETrain[2][-1],RMSETest[2][-1],RMSETest[2][-1]-RMSETrain[2][-1],std(mdl_3.get_residual(X_train,y_train)),std(mdl_3.trees[-1][0].get_leaf_values()),std(mdl_3.trees[-1][1].get_leaf_values()))+
            'XGB[%i]:  \t%.3f\t\t%.3f\t\t%.3f \r\n'%(max_depth,RMSETrain[3][-1],RMSETest[3][-1],RMSETest[3][-1]-RMSETrain[3][-1]))


except Exception as e:
    log(e)
    raise


Shape of X_train: 22865 9
Shape of X_test: 22865 9
prediciting using 1 trees
[Errno 2] No such file or directory: 'data10.dat'
prediciting using 1 trees
13719 13719
prediciting using 1 trees
computing last 1 trees of S [total trees: 2]
S Values before  [1.000000000000038]
S Values after  [0.1]
prediciting using 2 trees
rmse before: 5.119311921109777
prediciting using 2 trees
prediciting using 2 trees
rmse after: 5.943013066139404
prediciting using 2 trees
prediciting using 2 trees
prediciting using 2 trees
1 Back
prediciting using 1 trees
13719 13719
prediciting using 1 trees
computing last 1 trees of S [total trees: 2]
S Values before  [0.999999999999955]
S Values after  [0.1]
prediciting using 2 trees
rmse before: 5.13703255186678
prediciting using 2 trees
prediciting using 2 trees
rmse after: 5.948529639208775
prediciting using 2 trees
prediciting using 2 trees
prediciting using 2 trees
2 Back
prediciting using 1 trees
13719 13719
prediciting using 1 trees
computing last 1 trees of 

rmse before: 5.017092789366689
prediciting using 4 trees
prediciting using 4 trees
rmse after: 5.666909754529354
prediciting using 4 trees
prediciting using 4 trees
prediciting using 4 trees
2 Back
prediciting using 3 trees
13719 13719
prediciting using 1 trees
computing last 3 trees of S [total trees: 4]
S Values before  [0.09999999997953442, 0.09999999999517417, 0.09999999945106924, 0.09999999929992034, 0.09999999949491065, 0.09999999999998925, 0.0999999999106647, 0.09999999957302108, 0.09999999999488014, 0.09999999999854901, -0.00999999978585062, 0.09999881919708023, 0.099999999999988, 0.09999999955256866, 0.09999999901712246, 0.09999999811789109, 0.09999999999999999, 0.09999999999738982, 0.09999999999593624, 0.09999999999125728, 0.099999999996413, 0.0999999994744948, 0.09999999999393785, 0.09999990085038563, 0.09999999997869145, 0.0999999999959531, 0.09999999999837753, 0.0999999987881447, 0.09999999943916509, 0.09999999999999999, 0.09999999999121952, 0.09999999994639262, 0.09999999

rmse before: 4.94965076142337
prediciting using 5 trees
prediciting using 5 trees
rmse after: 5.526586263904746
prediciting using 5 trees
prediciting using 5 trees
prediciting using 5 trees
3 Back
[02:19:22] WARNING: C:/Jenkins/workspace/xgboost-win64_release_0.90/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
XGB
prediciting using 5 trees
prediciting using 5 trees
prediciting using 5 trees

-----------------------------------------------
ittr 4  	Train		Test		Diff		RVar	SVar	TVar
FGB[1]:  	5.543		5.578		0.034		5.543	0.032		3.532
FGB[10]:  	5.545		5.578		0.033		5.545	0.023		3.372
FGB[20]:  	5.530		5.563		0.033		5.530	0.032		2.959
XGB[5]:  	5.662		5.691		0.029 

prediciting using 5 trees
13719 13719
prediciting using 5 trees
computing last 1 trees of S [total trees: 6]
S Values before  [1.0707867475696784, 2.0352018748252867, 1.3409181656613565, 1.0036384089181476, -1.5325393323059764, 0.5325680497267744, 1.1981626341495863, 0.89004310737

rmse before: 4.948097915732569
prediciting using 6 trees
prediciting using 6 trees
rmse after: 5.445193775464575
prediciting using 6 trees
prediciting using 6 trees
prediciting using 6 trees
3 Back
[02:25:57] WARNING: C:/Jenkins/workspace/xgboost-win64_release_0.90/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
XGB
prediciting using 6 trees
prediciting using 6 trees
prediciting using 6 trees

-----------------------------------------------
ittr 5  	Train		Test		Diff		RVar	SVar	TVar
FGB[1]:  	5.431		5.474		0.044		5.431	0.027		3.402
FGB[10]:  	5.441		5.483		0.042		5.441	0.032		3.214
FGB[20]:  	5.429		5.469		0.040		5.429	0.040		3.342
XGB[5]:  	5.544		5.581		0.036 

prediciting using 6 trees
13719 13719
prediciting using 6 trees
computing last 1 trees of S [total trees: 7]
S Values before  [1.1886497085384298, -0.1745061142884081, 2.0984151925303114, 0.8785395635422435, 0.9052952584438196, 1.1504563104250398, 0.7254116311113284, 1.3194253090

rmse before: 4.8960340671916125
prediciting using 7 trees
prediciting using 7 trees
rmse after: 5.325045596973188
prediciting using 7 trees
prediciting using 7 trees
prediciting using 7 trees
3 Back
[02:32:27] WARNING: C:/Jenkins/workspace/xgboost-win64_release_0.90/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
XGB
prediciting using 7 trees
prediciting using 7 trees
prediciting using 7 trees

-----------------------------------------------
ittr 6  	Train		Test		Diff		RVar	SVar	TVar
FGB[1]:  	5.345		5.396		0.051		5.345	0.027		2.852
FGB[10]:  	5.353		5.407		0.054		5.353	0.040		2.826
FGB[20]:  	5.343		5.390		0.048		5.343	0.040		3.112
XGB[5]:  	5.441		5.485		0.044 

prediciting using 7 trees
13719 13719
prediciting using 7 trees
computing last 1 trees of S [total trees: 8]
S Values before  [1.2517962240011242, 0.9967754486454142, 0.801886333599816, 1.0712220458501098, 0.40813327960688817, 1.0480491376843009, 0.9126855983403644, 0.2348463177

...

rmse before: 3.666533954508546
prediciting using 146 trees
prediciting using 146 trees
rmse after: 3.635714440133671
prediciting using 146 trees
prediciting using 146 trees
prediciting using 146 trees
2 Back
prediciting using 145 trees
13719 13719
prediciting using 126 trees
computing last 20 trees of S [total trees: 146]
S Values before  [-0.009999999649347276, 0.09999999999999999, -0.009999992420369627, 0.09999999305015943, -0.009999999867377974, 0.09999999873066283, -0.009999999999999998, -0.009999995773675245, -0.009999999999999998, 0.0999999980145767, 0.09000000000000001, 0.09999999999999999, 0.09999998361584701, 0.09999999999980437, 0.09999999358538113, 0.0999999938015524, -0.009999999384073333, -0.009999993786352114, -0.009999999999999202, 0.09999991162759427, -0.009999993288531142, 0.09999999929495208, -0.009999999999999998, 0.09999999944290826, 0.09999999194427281, 0.09999999283388748, -0.009999977878720978, 0.004013209232217865, 0.09999999877283389, -0.009999999307059915, -0.

rmse before: 3.6309868401989
prediciting using 146 trees
prediciting using 146 trees
rmse after: 3.6434810352177687
prediciting using 146 trees
prediciting using 146 trees
prediciting using 146 trees
3 Back
[02:20:59] WARNING: C:/Jenkins/workspace/xgboost-win64_release_0.90/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
XGB
prediciting using 146 trees
prediciting using 146 trees
prediciting using 146 trees

-----------------------------------------------
ittr 145  	Train		Test		Diff		RVar	SVar	TVar
FGB[1]:  	3.642		4.157		0.514		3.642	0.054		2.852
FGB[10]:  	3.652		4.168		0.516		3.652	0.053		3.558
FGB[20]:  	3.642		4.148		0.506		3.642	0.051		3.033
XGB[5]:  	3.769		4.243		0.474 

prediciting using 146 trees
13719 13719
prediciting using 146 trees
computing last 1 trees of S [total trees: 147]
S Values before  [1.0026598649847873, 1.0942850611775046, 0.7374422980002312, 3.181242273323212, 0.42146192004072, 1.5909912679598484, 0.89021045712

rmse before: 3.6198971121964276
prediciting using 147 trees
prediciting using 147 trees
rmse after: 3.635547318882311
prediciting using 147 trees
prediciting using 147 trees
prediciting using 147 trees
2 Back
prediciting using 146 trees
13719 13719
prediciting using 127 trees
computing last 20 trees of S [total trees: 147]
S Values before  [0.09999999992973845, 0.09999999879077526, 0.0999999981967004, 0.09999999920689376, 0.09999999992416025, -0.00999999499991298, 0.09999999992167252, 0.09999999911123503, 0.09999999991978607, 0.09999999994645481, 0.09999999990691706, 0.09999999912515722, 0.09999999992605085, -0.009999999211312475, 0.0999999999302129, -0.009999999918002375, 0.09999999992112066, 0.09999999613994619, 0.099999999925213, -0.00999999992895738, -0.009999999927353943, 0.09999999992507648, -0.009999999786350033, 0.09999999895461795, 0.09000000000000001, -0.009999999877767195, 0.09999999990938674, -0.009999999924259583, -0.009999999546730937, 0.09000000000000001, -0.009999986579

rmse before: 3.5795637000805636
prediciting using 147 trees
prediciting using 147 trees
rmse after: 3.5945795363970783
prediciting using 147 trees
prediciting using 147 trees
prediciting using 147 trees
3 Back
[02:34:59] WARNING: C:/Jenkins/workspace/xgboost-win64_release_0.90/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
XGB
prediciting using 147 trees
prediciting using 147 trees
prediciting using 147 trees

-----------------------------------------------
ittr 146  	Train		Test		Diff		RVar	SVar	TVar
FGB[1]:  	3.640		4.155		0.515		3.640	0.040		2.296
FGB[10]:  	3.648		4.166		0.518		3.648	0.051		2.849
FGB[20]:  	3.640		4.147		0.506		3.640	0.053		2.513
XGB[5]:  	3.765		4.242		0.477 

prediciting using 147 trees


KeyboardInterrupt: 

In [319]:
print(X)
print(minus(Y,mdl.predict(X,1)))
for x,y in zip(X,minus(Y,mdl.predict(X,1))):
    if x[0]<8:
        print(x,y)

[[1], [7], [8], [3], [4], [10], [6], [8], [5], [3]]
prediciting using 2 trees
[0.0, 0.0, 3.333333333333333, 1.0, 0.0, 1.333333333333333, 1.0, -4.666666666666667, 0.0, -2.0]
prediciting using 2 trees
[1] 0.0
[7] 0.0
[3] 1.0
[4] 0.0
[6] 1.0
[5] 0.0
[3] -2.0


In [193]:
import urllib# url of the data
url = 'https://archive.ics.uci.edu/ml/machine-learning-databases/00265/CASP.csv'
# retrive data from the url and store in the folder name Data with filename as CASP.csv
urllib.request.urlretrieve (url, filename="CASP.csv" )

('CASP.csv', <http.client.HTTPMessage at 0x1b6360ea088>)

In [37]:
import pandas as pd
from sklearn.model_selection import train_test_split 
# Stratified sampling
from sklearn.model_selection import StratifiedShuffleSplit
df = pd.read_csv("CASP.csv")
labels = [1,2,3,4,5]
df['RMSD_cat'] = pd.cut(df['RMSD'], 5, labels=labels)
df.head()
# Create the instance from object
split = StratifiedShuffleSplit(n_splits=1, test_size=0.50, random_state=42)

# Create Train - Test Set
for train_index, test_index in split.split(df, df["RMSD_cat"]):
    train_set = df.loc[train_index]
    test_set = df.loc[test_index]

# Removing the RMSD_cat to give the original data
for _set in (train_set, test_set):
    _set.drop(["RMSD_cat"], axis=1, inplace=True)
    
# Creating new copies of Stratified Train and Test data
y_train = train_set["RMSD"].copy().values.tolist()
X_train = train_set.drop("RMSD", axis=1).values.tolist()

y_test = test_set["RMSD"].copy().values.tolist()
X_test = test_set.drop("RMSD", axis=1).values.tolist()
print("Shape of X_train:", len(X_train),len(X_train[0]))
print("Shape of X_test:",len(X_test),len(X_test[0]))
savedf()
type(X_train)

Shape of X_train: 22865 9
Shape of X_test: 22865 9


list

In [ ]:
def removeXY(node):
    if node == None:
        return
    node.X = node.Y = ''
    removeXY(node.Left)
    removeXY(node.Right)
import matplotlib.pyplot as plt
fig, ax = plt.subplots(figsize=(500, 500))
removeXY(mdl.trees[85][0])
mdl.trees[85][0].draw_tree(ax=ax)
plt.show()

